In [29]:
import pandas as pd
corpus = pd.read_csv(r"C:\Users\Eamon\Downloads\text_master.csv")
corpus

labels                                           big_text
0           0  hopson  a bill to be entitled an act relating ...
1           0  hochberg  a bill to be entitled an act relatin...
2           0  crabb  a bill to be entitled an act relating t...
3           0  morrison  a bill to be entitled an act relatin...
4           1  mccall  a bill to be entitled an act relating ...
...       ...                                                ...
44034       1    morales of maverick hb a noa 4667 a bill to ...
44035       1    murr hb a noa 4668 a bill to be entitled an ...
44036       1    cain hb a noa 4669 a bill to be entitled an ...
44037       0    capriglione hb a noa 4670 a bill to be entit...
44038       0    a johnson of harris hb a noa 4671 a bill to ...

[44039 rows x 2 columns]

In [31]:
for x in indices_remove:
    corpus = corpus.drop(index=x)

In [32]:
indices_remove = []
for x in range(len(corpus['big_text'])):
    if(not isinstance(corpus.iloc[x]['big_text'], str)):
        indices_remove.append(x)
        print(corpus.iloc[x]['big_text'])
        
indices_remove

[]

In [33]:
type(corpus)

pandas.core.frame.DataFrame

In [34]:
corpus = corpus[:5000]

In [35]:
type(corpus)

pandas.core.frame.DataFrame

In [56]:
corpus['big_text']

0       hopson  a bill to be entitled an act relating ...
1       hochberg  a bill to be entitled an act relatin...
2       crabb  a bill to be entitled an act relating t...
3       morrison  a bill to be entitled an act relatin...
4       mccall  a bill to be entitled an act relating ...
                              ...                        
4995    naishtat  a bill to be entitled an act relatin...
4996    hupp  a bill to be entitled an act relating to...
4997    chavez  a bill to be entitled an act relating ...
4998    branch  a bill to be entitled an act relating ...
4999    eissler  a bill to be entitled an act relating...
Name: big_text, Length: 5000, dtype: object

In [57]:
corpus['big_text'] = np.array([corpus['big_text']]).flatten()

In [59]:
array = np.array([corpus['big_text']]).flatten()

In [60]:
array

array(['hopson  a bill to be entitled an act relating to the creation administration powers duties operation and financing of the houston county groundwater conservation district be it enacted by the legislature of the state of texas definitions in this act "board" means the board of directors of the houston county groundwater conservation district "designated management area" means an area designated as a management area under  water code "director" means a member of the board "district" means the houston county groundwater conservation district creation  a groundwater conservation district to be known as the houston county groundwater conservation district is created in houston county subject to approval at a confirmation election under section10 of this act the district is a governmental agency and a political subdivision of this state findings of benefit and public purpose  the district is created to serve a public use and benefit the district is created under and is essential to a

In [61]:
count = 0
for label in corpus['labels']:
    if label == 1:
        count += 1

print(len(corpus))
print(count)
print(1 - (count / 5000))

5000
1011
0.7978000000000001


In [62]:
import numpy as np
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(corpus['big_text'], 
                                                    corpus['labels'], test_size=0.2,
                                                    random_state=42)


In [81]:
X_test

<tf.Tensor: shape=(1000,), dtype=string, numpy=
array([b'isett  a bill to be entitled an act relating to the repeal of the franchise tax be it enacted by the legislature of the state of texas chapter171 tax code is repealed  ',
       b'pena  a bill to be entitled an act relating to the use of proceeds from criminal asset forfeiture to fund certain activities sponsored or conducted by the texas commission on alcohol and drug abuse be it enacted by the legislature of the state of texas article 5906 code of criminal procedure is amended by amending sub  and  and adding subsection to read as follows the governing body of a political subdivision may not use funds received under this subchapterfor programs or facilities listed under subsection or  sub - if an officer of or member of the board of directors of the entity providing the program or facility is related to a member of the governing body the attorney representing the state or the head of the law enforcement agency within the third 

In [64]:
type(X_train)

pandas.core.series.Series

In [65]:
import tensorflow as tf
X_train_tensor = tf.convert_to_tensor(X_train)
X_test = tf.convert_to_tensor(X_test)
y_train = tf.convert_to_tensor(y_train)
y_test = tf.convert_to_tensor(y_test)

In [66]:
X_train_tensor

<tf.Tensor: shape=(4000,), dtype=string, numpy=
array([b'solomons  a bill to be entitled an act relating to prohibiting certain disruptions at a funeral service creating an offense be it enacted by the legislature of the state of texas chapter42 penal code is amended by adding  to read as follows funeral service disruptions  in this section"facility" means a building at which any portion of a funeral service takes place including a funeral parlor mortuary private home or established place of worship "funeral service" means a ceremony procession or memorial service including a wake or viewing held in connection with the burial or cremation of the dead "picketing" means standing sitting or repeated walking riding driving or other similar action by a person displaying or carrying a banner placard or sign engaging in loud singing chanting whistling or yelling with or without noise amplification through a device such as a bullhorn or microphone or blocking access to a facility or cemetery b

In [72]:
vocab_size = 4000
text_vec_layer = tf.keras.layers.TextVectorization(max_tokens=vocab_size, 
                                                   output_mode="tf_idf")
text_vec_layer.adapt(np.array([corpus['big_text']]).flatten())
#text_vec_layer.adapt(corpus['big_text'])

In [73]:
text_vec_layer

In [74]:
text_vec_layer(["to", "the"])

<tf.Tensor: shape=(2, 4000), dtype=float32, numpy=
array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.69304717, 0.        , ..., 0.        , 0.        ,
        0.        ]], dtype=float32)>

In [77]:
embed_size = 64
tf.random.set_seed(42)
model = tf.keras.Sequential([
    text_vec_layer,
    tf.keras.layers.Embedding(vocab_size, embed_size, mask_zero=True),
    tf.keras.layers.LSTM(128, dropout=0.2),
    tf.keras.layers.Dense(1, activation="sigmoid")
])
model.compile(loss="binary_crossentropy", optimizer="nadam",
              metrics=["accuracy"])

early_stopping_cb = tf.keras.callbacks.EarlyStopping(
    monitor="accuracy", patience=5, restore_best_weights=True)

history = model.fit(X_train_tensor, y_train, validation_data=(X_test, y_test), epochs=20, 
                    verbose=1)

Epoch 1/20
  4/125 [..............................] - ETA: 14:24 - loss: 0.6798 - accuracy: 0.7500

InvalidArgumentError: Graph execution error:

Detected at node 'sequential_9/embedding_9/embedding_lookup' defined at (most recent call last):
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\runpy.py", line 196, in _run_module_as_main
      return _run_code(code, main_globals, None,
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\runpy.py", line 86, in _run_code
      exec(code, run_globals)
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
      app.launch_new_instance()
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\site-packages\traitlets\config\application.py", line 982, in launch_instance
      app.start()
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\site-packages\ipykernel\kernelapp.py", line 712, in start
      self.io_loop.start()
    File "C:\Users\Eamon\AppData\Local\Programs\Python\Python310\lib\site-packages\to